In [ ]:
!pip install umap
!pip install trimap
!pip3 install tsnecuda==3.0.1+cu111 -f https://tsnecuda.isx.ai/tsnecuda_stable.html
!pip install nltk
!pip install gensim

%load_ext autoreload
%autoreload 2
from google.colab import drive
drive.mount('/content/drive', force_remount=True)
import sys
sys.path.insert(1, r'/content/drive/MyDrive/STU_Rafae_Baez_Ramirez/New_SNE_Code/')
sys.path.insert(1, r'/content/drive/MyDrive/STU_Rafae_Baez_Ramirez/New_SNE_Code/LAPS_and_GAPS-master/')
#sys.path.insert(1, r'C:/Users/baezr/PythonCode/New_SNE_Code/')
#sys.path.insert(1, r'C:/Users/baezr/PythonCode/New_SNE_Code/LAPS_and_GAPS-master/')
## Importing libraries

%matplotlib inline
import warnings
warnings.filterwarnings('ignore')

import os
import sys
import math
import time
import numpy as np
import pandas as pd
from bokeh.io import show, output_notebook, curdoc
from bokeh.plotting import figure
from bokeh.plotting import figure, output_file, show, ColumnDataSource
from bokeh.models import HoverTool
from bokeh.io import output_notebook
from bokeh.models.glyphs import Text
from bokeh.layouts import row
from bokeh.io import export_png
output_notebook()

## Importing local Python files

sys.path.append(r'../')
#%cd /content/drive/MyDrive/STU_Rafae_Baez_Ramirez/New_SNE_Code/LAPS_and_GAPS-master
from src import Preprocessing, Distances, Explanation, DR_algorithms, genericMethods
from src.LAPS_tabular import LapsExplainer
from src.GAPS_tabular import GapsExplainer
from src.GAPS_Explanation import get_local_explanations_for_GAPS, compute_local_divergences

## Defining input paths (Update the Data_path attribute accordingly)
def is_notebook():
  try:
    shell = get_ipython().__class__.__name__
    if shell == 'ZMQInteractiveShell':
      return True   # Jupyter notebook or qtconsole
    elif shell == 'TerminalInteractiveShell':
      return False  # Terminal running IPython
    else:
      return False  # Other type (?)
  except NameError:
    return False
if is_notebook():
    from tqdm.notebook import tqdm
else:
    from tqdm import tqdm

In [ ]:
#Data_path = r'C:/Users/baezr/PythonCode/New_SNE_Code/LAPS_and_GAPS-master/data/'
Data_path = r'/content/drive/MyDrive/STU_Rafae_Baez_Ramirez/New_SNE_Code/LAPS_and_GAPS-master/data/'

In [ ]:
def LAPS_and_plot(embedding, data_transformed, data_df, y_res, model_feats, targ, cat_feats, cat_names, num_feats, points, neighbors = 20, show_fig = False, verbose = False):
  exp = LapsExplainer(data_df.values, feature_names=model_feats, class_names=targ,
                      categorical_features=cat_feats, categorical_names=cat_names,
                      discretize_continuous=False, discretizer='quartile', random_state=42)
  laps_scores_all = []
  comp_scores_all = []
  #for i, point in enumerate(points):
  bar = tqdm(range(len(points)))

  for i in bar:
    point = points[i]
    #print(f'Processing point {i}/{len(points)}')
    start = time.time()
    neigh, neigh_emb, over_data, over_data_emb = exp.generate_perturbed_neighborhood(data_df.values, data_transformed, embedding,
                                                                                    point, data_df.values[point], nbrs=neighbors,
                                                                                    num_features=5, verbose = verbose)
    corr_feat_dist, _, _, _, _ = Explanation.explain_point_local(data_df.values[point], neigh, over_data,
                                                                model_feats, cat_feats, num_feats)
    corr_feat_dist_embd, _, _, _, _ = Explanation.explain_point_local(data_df.values[point], neigh_emb, over_data_emb,
                                                                      model_feats, cat_feats, num_feats)
    components, divergence = Explanation.compute_local_divergence(corr_feat_dist, corr_feat_dist_embd,
                                                                  neigh, neigh_emb)
    components = components.split(",")
    laps_scores_all.append(divergence)
    comp_scores_all.append(components)
    #bar.set_descriptions(f'Working on POI {i}/{len(points)}')
  if show_fig:
    idx = [i for i in range(len(y_res))]
    colormap = {99: 'Red',
                -1: 'white',
                0: 'gold',
                1: 'peachpuff',
                2: 'indigo',
                3: 'green',
                4: 'darkolivegreen',
                5: 'cyan',
                6: 'blue',
                7: 'lightsteelblue',
                8: 'magenta',
                9: 'grey',
                98: 'limegreen'}
    colors = [colormap[z] for z in y_res.ravel()]
    labels = {99: 'POI',
                -1: 'Class -1',
                0: 'Class 0',
                1: 'Class 1',
                2: 'Class 2',
                3: 'Class 3',
                4: 'Class 4',
                5: 'Class 5',
                6: 'Class 6',
                7: 'Class 7',
                8: 'Class 8',
                9: 'Class 9',
                98: 'neighborsPOI'}
    annotations = [labels[z] for z in y_res.ravel()]
    source = ColumnDataSource(
          data=dict(
              x=embedding[:,0],
              y=embedding[:,1],
              all_colors = colors,
              label = annotations,
              indexes = idx
          )
      )
    hover = HoverTool(
          tooltips=[
              ("index", "$index"),
              ("(x,y)", "($x, $y)"),
          ]
      )
    curdoc().theme = 'dark_minimal'
    p = figure(plot_width=700, plot_height=450, tools=[hover],
            title="Embedding")
    glyph = Text(x="x", y="y", x_offset=7, y_offset=7, text_font_size="9pt", text_color="grey") # text='indexes'
    p.circle('x', 'y', fill_color='all_colors', line_color='white', legend='label', size=10, source=source)
    p.add_glyph(source, glyph)
    print('Showing Plot')
    show(p)
  return comp_scores_all, laps_scores_all

In [ ]:
import nltk
from nltk.tokenize import sent_tokenize, word_tokenize
nltk.download('punkt')
from gensim.models import Word2Vec

df = pd.read_csv(Data_path + 'spam.csv', encoding = "ISO-8859-1")
labels = np.expand_dims(df['v1'].to_numpy(), -1)
raw_data = df['v2'].to_numpy()
data = []
#print(raw_data)
for sentence in raw_data:
  aux = []
  for word in word_tokenize(sentence):
    aux.append(word.lower())
  data.append(aux)
dims = 100
model = Word2Vec(data, min_count = 1, size = dims, window = 5)
new_data = np.array([np.mean([model[w] for w in sentence if w in model] or [np.zeros(dims)], axis = 0)
                     for sentence in data])
new_labels = np.zeros(labels.shape)
new_labels[labels == 'spam'] = 1
spam_data = np.hstack([new_data, new_labels])
print(spam_data.shape)

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


(5572, 101)


In [ ]:
df = pd.read_csv(Data_path + 'sentiment.csv', encoding = "ISO-8859-1", header = None)
df.columns = ['target','id','date','flag','user','text']
df = df.sample(10000)
labels = np.expand_dims(df['target'].to_numpy(), -1)
raw_data = df['text'].to_numpy()
data = []
#print(raw_data)
for sentence in raw_data:
  aux = []
  for word in word_tokenize(sentence):
    aux.append(word.lower())
  data.append(aux)
dims = 100
model = Word2Vec(data, min_count = 1, size = dims, window = 5)
new_data = np.array([np.mean([model[w] for w in sentence if w in model] or [np.zeros(dims)], axis = 0)
                     for sentence in data])
new_labels = np.zeros(labels.shape)
new_labels[labels == 2] = 1
new_labels[labels == 4] = 2
sentiment_data = np.hstack([new_data, new_labels])
print(sentiment_data.shape)

(10000, 101)


In [ ]:
print(df['target'][:15])
print(sentiment_data[:, -1][:15])

168767     0
84779      0
1201163    4
353937     0
674372     0
1136538    4
767090     0
857989     4
701481     0
380065     0
698615     0
1483195    4
155425     0
1248303    4
788431     0
Name: target, dtype: int64
[0. 0. 2. 0. 0. 2. 0. 2. 0. 0. 0. 2. 0. 2. 0.]


In [ ]:
from sklearn.neighbors import kneighbors_graph as KNN
percPOI = 0.10

k=50
df = pd.DataFrame(spam_data)
# df = pd.read_csv(Data_path+'breast_cancer.csv')
# df= pd.read_csv(Data_path+'Wine_Quality.csv')
#df = pd.read_csv(Data_path+'Credit_card.csv')
#df = pd.read_csv(Data_path+'Magic.csv')
df = df.fillna(0)
# df = df.sample(200)
#df = df.sample(1000)
#df = df.sample(5000)
df.reset_index(inplace= True, drop= True)
df.head()
print(df.shape)
## Identify intrinsic dimensionality using: the Maximum likelihood intrinsic dimensionality estimator

#int_dim = Preprocessing.repeated(Preprocessing.intrinsic_dim_scale_interval, df.values,mode='bootstrap', nb_iter=500, verbose=1,
                            #  k1=10, k2=20)
#print ("Intrinsic dimensionality:", int_dim)

model_features, target = Preprocessing.set_features_and_target(df)

y = (df[target].values.reshape(-1, ))
X_df = pd.DataFrame(df, columns=model_features)

np.random.seed(2022)
#amountOfPOI = int(X_df.shape[0]*percPOI)
amountOfPOI = 200
POI = np.random.randint(0, X_df.shape[0], amountOfPOI)
print(np.sort(POI))
# POI = [24,86]
categorical_features = []
numeric_features = []
categorical_names = []

X_transformed, categorical_features, numeric_features, categorical_names = Preprocessing.identify_and_transform_features(df, model_features)

# n_samples = X_transformed.shape[0]
# distance_matrix = KNN(X=X_transformed, n_neighbors=n_samples-1, mode='distance', include_self=False, n_jobs=-1)
# distance_matrix_POI = distance_matrix[POI].toarray()
# all_dist_based_NN_POI = distance_matrix_POI.argsort()[:,1:]


#new_y = np.copy(y)
#for i in POI:
#  new_y[i] = 99

# def flatten_list(l): return [item for sublist in l for item in sublist]
# neighborsPOI = flatten_list(all_dist_based_NN_POI[:,:k])

# for i in neighborsPOI:
#   new_y[i] = 98
# print(f'POI: {POI}')


params = [X_df, y, model_features, target, categorical_features, categorical_names, numeric_features, POI]

(5572, 101)
Features:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99]
Target:  [100]
[  11   24   31   48   62   83   90  129  147  173  195  211  250  269
  301  340  378  488  501  504  508  533  576  707  772  773  858  871
  880  905  910  996 1003 1024 1077 1154 1184 1199 1208 1232 1234 1244
 1279 1305 1306 1347 1399 1402 1445 1476 1481 1488 1488 1501 1502 1552
 1571 1599 1602 1621 1635 1666 1697 1697 1889 1929 1950 1985 1990 2021
 2034 2060 2066 2085 2094 2124 2145 2195 2235 2238 2311 2320 2357 2467
 2487 2508 2605 2610 2711 2776 2801 2804 2849 2862 2903 2903 2907 2909
 2938 2946 2973 3028 3062 3077 3096 3124 3138 3153 3155 3179 3198 3204
 32

In [ ]:

from sklearn.manifold import TSNE as sklearnTSNE

embed_tsne = sklearnTSNE(n_components=2, perplexity=50).fit_transform(X_transformed)

In [ ]:
comp, div = LAPS_and_plot(embed_tsne, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], neighbors = 50, show_fig = True, verbose = False)

#print(div)
print(f'Average LAPS divergence over all POI : {np.mean(np.array(div)):.5f}')


100%|██████████| 200/200 [12:47<00:00,  3.84s/it]

Showing Plot


Average LAPS divergence over all POI : 0.70836


In [ ]:
from fSNE_torch import fSNE_torch as fSNE_fast
fSNE_fast_obj = fSNE_fast(X_transformed, max_iter = 1000, POI=POI, perp = 50.0, lambdas = 2)
embed_fsne_fast = fSNE_fast_obj.fit_transform()

using cuda
Cost: 4912.34936: 100%|██████████| 1000/1000 [06:24<00:00,  2.60it/s]


In [ ]:
comp, div = LAPS_and_plot(embed_fsne_fast, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], neighbors = 50, show_fig = True, verbose = False)
#print(div)
print(f'Average LAPS divergence over all POI : {np.mean(np.array(div)):.5f}')

100%|██████████| 200/200 [12:46<00:00,  3.83s/it]

Showing Plot


Average LAPS divergence over all POI : 0.71211


In [ ]:
to_file = [embed_fsne_fast, div, params[1], POI]
np.save('spam_50p_50n', to_file)

In [ ]:

def GAPS_score(embedding, data_df, data_transformed, model_feats, target, cat_feats, cat_names, num_feats, POI = None, show_fig = False, verbose = False):
  if POI is None:
    rep_subset = genericMethods.generate_representative_subset(18, data_df)
    data_instance_numbers = rep_subset[0]
  else:
    data_instance_numbers = POI
  #print(data_instance_numbers)
  explainer = GapsExplainer(data_df.values, feature_names=model_feats,
                            class_names=target, categorical_features=cat_feats,
                            discretize_continuous=False, discretizer='quartile',
                            random_state=42)
  neigh, neigh_emb, over_data, over_data_emb, local_feat_cont, local_feat_cont_emb, neigh_local, neigh_emb_local = explainer.generate_perturbed_neighborhood_global(
      data_df.values, data_transformed, embedding, data_instance_numbers, model_feats, cat_feats, num_feats, nbrs = 5, num_features = 5, verbose = False)
  local_divergences = compute_local_divergences(neigh_local, neigh_emb_local, local_feat_cont, local_feat_cont_emb)
  corr_feat_dist, _, _ = Explanation.explain_point_global(over_data, model_feats, cat_feats, num_feats)
  corr_feat_dist_embd, _, _ = Explanation.explain_point_global(over_data_emb, model_feats, cat_feats, num_feats)
  components, overall_divergence = Explanation.compute_global_divergence(corr_feat_dist, corr_feat_dist_embd, neigh, neigh_emb, local_divergences)
  components = components.split(',')
  return components, overall_divergence, POI


In [ ]:
!pip install mnist

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
import mnist
train_images = mnist.train_images()
train_labels = mnist.train_labels()

test_images = mnist.test_images()
test_labels = mnist.test_labels()

X_train = train_images.reshape(-1, 28*28)
X_test = test_images.reshape(-1,28*28)

all_train = np.hstack((X_train, train_labels.reshape(-1,1)))

print(all_train.shape)
print(X_train.shape)
print(train_labels.shape)
print(X_test.shape)
print(test_labels.shape)

(60000, 785)
(60000, 784)
(60000,)
(10000, 784)
(10000,)


In [ ]:
means = np.mean(all_train, axis = 0)
#print(means.shape)
same = np.argwhere(np.logical_or(means == 0, means == 1))
print(same.shape)
new_data = np.delete(all_train, same, axis = 1)
print(new_data.shape)
print(np.max(new_data[:,:-1]))

(67, 1)
(60000, 718)
255


In [ ]:
from fSNE_torch import fSNE_torch as fSNE_fast
from fSNEparallel import fSNE as fSNE_parallel
from sklearn.manifold import TSNE as sklearnTSNE
from my_SNE import My_SNE

##TSNE

In [ ]:
start = time.time()
from sklearn.manifold import TSNE as sklearnTSNE

embed_tsne = TSNE(n_components=2, learning_rate=0.1,perplexity=10, n_iter= iterations,verbose=True).fit_transform(X_transformed)
#embed_tsne = sklearnTSNE(n_components=2, perplexity=10).fit_transform(X_transformed)

print(f'That took {(time.time()-start):.4f} seconds')
print(categorical_features)
comp, div = LAPS_and_plot(embed_tsne, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], show_fig = True, verbose = False)

print(div)
print(np.mean(np.array(div)))


NameError: ignored

In [ ]:
start = time.time()
embed_tsne = TSNE(n_components=2, learning_rate=0.1, perplexity=12, n_iter= iterations,verbose=True).fit_transform(X_transformed)
print(f'That took {(time.time()-start):.4f} seconds')
print(categorical_features)
comp, div = LAPS_and_plot(embed_tsne, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], show_fig = True, verbose = False)

print(div)
print(np.mean(np.array(div)))


That took 3.4170 seconds
[]
Getting first time distances for data
Getting first time distances for embedded data
Showing Plot


[0.7808071575830353, 0.7262832382465028, 0.7666351011380665, 0.6521697195321099, 0.757261494123757, 0.6656845591185949, 0.7320632355103589, 0.7774383257805151, 0.723108734566656, 0.6813854449467763, 0.6264841223316052, 0.7852470096850199, 0.7052962331908605, 0.7586515007023096, 0.7610172104010344, 0.7275150972105824, 0.6771231850528545, 0.8238429279127697, 0.6084016706417772, 0.5598341922861262, 0.6572763797453465, 0.4782008631979833, 0.7356206043619329, 0.6865272404825986, 0.7556513669533536, 0.7194684662748354, 0.7244419610770176, 0.6047997660015989, 0.687236442939853, 0.625787495308547, 0.6556016574683972, 0.752112559421362, 0.7570722701946135, 0.5793596327676246, 0.7644180285169042, 0.7198019931989041, 0.7214989516629737, 0.6207649742142178, 0.6347146610254581, 0.7335871083953656, 0.651969101198917, 0.7033422367784303, 0.6969134889969129, 0.6741697222311989, 0.6612339162664358, 0.6688791023987727, 0.7335382706705127, 0.6935153334827112, 0.6585138503684613, 0.6026664017474369, 0.695

In [ ]:
start = time.time()
embed_tsne = TSNE(n_components=2, learning_rate=0.1, perplexity=50, n_iter= iterations,verbose=True).fit_transform(X_transformed)
print(f'That took {(time.time()-start):.4f} seconds')
print(categorical_features)
comp, div = LAPS_and_plot(embed_tsne, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], show_fig = True, verbose = False)

print(div)
print(np.mean(np.array(div)))

That took 3.6773 seconds
[]
Getting first time distances for data
Getting first time distances for embedded data
Showing Plot


[0.8179989480352932, 0.7916766676715103, 0.8577958934730756, 0.617632593117371, 0.6978498474908941, 0.7945260878774767, 0.7647380806712709, 0.7448283468673984, 0.8442154819778771, 0.7990736819636481, 0.7596996780656116, 0.8207011567352103, 0.8248941515490396, 0.7461322424200367, 0.6956013681341452, 0.7623190151312302, 0.8062773893239106, 0.7884486724711293, 0.7504688735635017, 0.6531745568480434, 0.7890826676607288, 0.6509060392593045, 0.7308358252018339, 0.7141317510318247, 0.8538878214910983, 0.8155050850563652, 0.8152981166706506, 0.8022621856868566, 0.7600068489995624, 0.7722882555230326, 0.7535338003046723, 0.7838606083125561, 0.7887335229856283, 0.6847531974045058, 0.8000093404267787, 0.821265349109215, 0.6527501720611004, 0.7638539659132366, 0.6656727960031312, 0.7967654495145919, 0.7529173008121695, 0.6695856521864672, 0.6621840489900441, 0.7387923155749991, 0.7479659041033049, 0.7315235542381695, 0.83135248733335, 0.7610547003069039, 0.6901785224800463, 0.7715554789147558, 0.6

BREAST CANCER

In [ ]:
start = time.time()
embed_tsne = TSNE(n_components=2, learning_rate=0.1, perplexity = 12, n_iter= iterations,verbose=True).fit_transform(X_transformed)
print(f'That took {(time.time()-start):.4f} seconds')
print(categorical_features)
comp, div = LAPS_and_plot(embed_tsne, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], show_fig = True, verbose = False)

print(div)
print(np.mean(np.array(div)))


That took 7.5902 seconds
[]


100%|██████████| 200/200 [03:53<00:00,  1.17s/it]

Showing Plot


[0.8015775769663102, 0.8004743198142329, 0.8187241214619707, 0.7731257749639867, 0.785997844866344, 0.8214028859824314, 0.7585109725942754, 0.8085890193087251, 0.8204545284605342, 0.8385848459828962, 0.8109949711293156, 0.8191042530273436, 0.8216651892176079, 0.8258918648161152, 0.7958335494963027, 0.8416433901098985, 0.8366191809108767, 0.8358921452494394, 0.8455471057230924, 0.8405327950874572, 0.8166784540875843, 0.8413131626253769, 0.8359102068478976, 0.8059903511073899, 0.8218629229919153, 0.8535816180209255, 0.8514330055785202, 0.7757738945328989, 0.8067216778623721, 0.8192221305007509, 0.8357510646332308, 0.7995463462953457, 0.811663370367961, 0.7883402008135016, 0.8133107209828461, 0.8376893441853868, 0.8263779440401124, 0.8181990843527607, 0.8063108499190874, 0.7997734987073788, 0.7949984902108045, 0.8078048765912726, 0.8119169273273823, 0.779567994171835, 0.8064485001104754, 0.799400766187333, 0.8197374877046533, 0.7935025905595128, 0.8041791176442976, 0.8097445091600055, 0.7

WINE QUALITY

In [ ]:
start = time.time()
embed_tsne = TSNE(n_components=2, learning_rate=0.1, perplexity = 12, n_iter= iterations,verbose=True).fit_transform(X_transformed)
print(f'That took {(time.time()-start):.4f} seconds')
#print(categorical_features)
comp, div = LAPS_and_plot(embed_tsne, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], show_fig = True, verbose = False)

print(div)
print(np.mean(np.array(div)))


NameError: ignored

CREDIT CARD

In [ ]:
start = time.time()
embed_tsne = TSNE(n_components=2, learning_rate=0.1, perplexity = 12, n_iter= iterations,verbose=True).fit_transform(X_transformed)
print(f'That took {(time.time()-start):.4f} seconds')
#print(categorical_features)
comp, div = LAPS_and_plot(embed_tsne, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], show_fig = True, verbose = False)

print(div)
print(np.mean(np.array(div)))


NameError: ignored

MAGIC

In [ ]:
start = time.time()
embed_tsne = TSNE(n_components=2, learning_rate=0.1, perplexity = 12, n_iter= iterations,verbose=True).fit_transform(X_transformed)
print(f'That took {(time.time()-start):.4f} seconds')
#print(categorical_features)
comp, div = LAPS_and_plot(embed_tsne, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], show_fig = True, verbose = False)

print(div)
print(np.mean(np.array(div)))


That took 1.8368 seconds
Getting first time distances for data
Getting first time distances for embedded data
Showing Plot


[0.8135968551626023, 0.8502856763003923, 0.8037909866672619, 0.8746057372584275, 0.7919223213375397, 0.8325062761509827, 0.8724219583560089, 0.8617734922953113, 0.7826299798182326, 0.874201235496944, 0.896624415257834, 0.8045771945221429, 0.855519735379024, 0.8310788414431471, 0.8662738082400907, 0.8363732383355558, 0.8839925335653878, 0.7105193774504948, 0.8459569916123966, 0.8619958463664044, 0.786852367814822, 0.830166894553221, 0.850458635535593, 0.8282408923691811, 0.7086369198848451, 0.8681581316385698, 0.8547284286463057, 0.6113735242216852, 0.8188053643311943, 0.8519435761730392, 0.8428530429600285, 0.8341269370066022, 0.8647559544000842, 0.8193233066627423, 0.885839047621366, 0.8605176189236314, 0.8050763743836109, 0.8864656931249137, 0.8922603923551136, 0.8039324149208735, 0.8452609037411833, 0.8759343710694236, 0.8633719665643926, 0.8648891811820669, 0.8764977720290987, 0.8796561865958274, 0.8458032580175436, 0.865598180416723, 0.8634314102385372, 0.7937513775765861, 0.88737

#### My_SNE

In [ ]:
SNE = My_SNE(X_transformed.T, max_iterations = iterations)
start = time.time()
embed_sne = SNE.fit_transform()
#p_matrix = SNE.fit_transform()
print(f'That took {(time.time()-start):.4f} seconds')
comp, div = LAPS_and_plot(embed_sne, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], show_fig = True, verbose = False)
print(div)
print(np.mean(np.array(div)))
#print(global_div)


Calculating p for all pairs...
---processing for image 0
---processing for image 1
---processing for image 2
---processing for image 3
---processing for image 4
---processing for image 5
---processing for image 6
---processing for image 7
---processing for image 8
---processing for image 9
---processing for image 10
---processing for image 11
---processing for image 12
---processing for image 13
---processing for image 14
---processing for image 15
---processing for image 16
---processing for image 17
---processing for image 18
---processing for image 19
---processing for image 20
---processing for image 21
---processing for image 22
---processing for image 23
---processing for image 24
---processing for image 25
---processing for image 26
---processing for image 27
---processing for image 28
---processing for image 29
---processing for image 30
---processing for image 31
---processing for image 32
---processing for image 33
---processing for image 34
---processing for image 35
---proc

ValueError: ignored

#### SNE (torch)

In [ ]:
SNE = TorchSNE(verbose = True, n_iter = iterations)
start = time.time()
embed_sne = SNE.fit_transform(X_transformed)
print(f'That took {(time.time()-start):.4f} seconds')
#constants = [X_df, new_y, model_features, target, categorical_features, categorical_names, numeric_features, POI]
comp, div = LAPS_and_plot(embed_sne, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], constants[7], show_fig = True, verbose = False)
# global_comp, global_div, _ = GAPS_score(embed_sne, constants[0], X_transformed,
#                                         constants[2], constants[3],
#                                         constants[4], constants[5],
#                                         constants[6], constants[7], show_fig = False)

print(div)
# print(global_div)

using cpu
initializing...
computing p-values...
fiting...
error: 50.703: 100%|█████████████████████████████████████████████████████████████████| 100/100 [00:01<00:00, 69.40it/s]


That took 1.4560 seconds


IndexError: ignored

In [ ]:
print(f'Avg Laps was {np.mean(np.array(div))}')

Avg Laps was 0.7800961484554481


In [ ]:
SNE = TorchSNE(verbose = True, n_iter = iterations)
start = time.time()
embed_sne1 = SNE.fit_transform(X_transformed)
print(f'That took {(time.time()-start):.4f} seconds')
comp, div = LAPS_and_plot(embed_sne1, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], show_fig = True, verbose = False)
print(div)
print(np.mean(np.array(div)))
# print(global_div)

using cuda
initializing...
computing p-values...
fiting...
error: nan: 100%|██████████| 200/200 [00:00<00:00, 261.27it/s]


That took 0.9455 seconds


In [ ]:
SNE = TorchSNE(verbose = True, n_iter = iterations)
start = time.time()
embed_sne2 = SNE.fit_transform(X_transformed)
print(f'That took {(time.time()-start):.4f} seconds')
#constants = [X_df, new_y, model_features, target, categorical_features, categorical_names, numeric_features, POI]
comp, div = LAPS_and_plot(embed_sne2, X_transformed,
              constants[0], constants[1],
              constants[2], constants[3],
              constants[4], constants[5],
              constants[6], constants[7][0], show_fig = True, verbose = False)
# global_comp, global_div, _ = GAPS_score(embed_sne, constants[0], X_transformed,
#                                         constants[2], constants[3],
#                                         constants[4], constants[5],
#                                         constants[6], constants[7], show_fig = False)

print(div)
# print(global_div)

using cuda
initializing...
computing p-values...
fiting...
error: 28.954: 100%|██████████| 50/50 [00:00<00:00, 228.16it/s]


That took 0.2282 seconds


0.7272008957382724


In [ ]:
def showfig(y_res, embedding):
  idx = [i for i in range(len(y_res))]
  colormap = {-1: 'Red',
              0: 'gold',
              1: 'peachpuff',
              2: 'indigo',
              3: 'green',
              4: 'darkolivegreen',
              5: 'cyan',
              6: 'blue',
              7: 'lightsteelblue',
              8: 'magenta',
              9: 'grey',
              -9: 'limegreen'}
  colors = [colormap[z] for z in y_res.ravel()]
  labels = {-1: 'POI',
              0: 'Class 0',
              1: 'Class 1',
              2: 'Class 2',
              3: 'Class 3',
              4: 'Class 4',
              5: 'Class 5',
              6: 'Class 6',
              7: 'Class 7',
              8: 'Class 8',
              0: 'Class 9',
              -9: 'neighborsPOI'}
  annotations = [labels[z] for z in y_res.ravel()]
  source = ColumnDataSource(
        data=dict(
            x=embedding[:,0],
            y=embedding[:,1],
            all_colors = colors,
            label = annotations,
            indexes = idx
        )
    )
  hover = HoverTool(
        tooltips=[
            ("index", "$index"),
            ("(x,y)", "($x, $y)"),
        ]
    )
  curdoc().theme = 'dark_minimal'
  p = figure(plot_width=700, plot_height=450, tools=[hover],
          title="Embedding")
  glyph = Text(x="x", y="y", x_offset=7, y_offset=7, text_font_size="9pt", text_color="grey") # text='indexes'
  p.circle('x', 'y', fill_color='all_colors', line_color='white', legend='label', size=10, source=source)
  p.add_glyph(source, glyph)
  print('Showing Plot')
  show(p)

#### TSNE (cuda)

In [ ]:
start = time.time()
embed_tsne = TSNE(n_components=2, learning_rate=0.1,perplexity=5, n_iter= iterations,verbose=True).fit_transform(X_transformed)
print(f'That took {(time.time()-start):.4f} seconds')
comp, div = LAPS_and_plot(embed_tsne, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], show_fig = True, verbose = False)
print(div)
print(np.mean(np.array(div)))

That took 3.0646 seconds
Getting first time distances for data
Getting first time distances for embedded data
Showing Plot


[0.8573594164291976, 0.7841556687212934, 0.865074533461017, 0.810512819247978, 0.8588593435141771, 0.8210337538240231, 0.8646144470084571, 0.8537009447485162, 0.8321813272624101, 0.775891725327251, 0.7936349078477096, 0.8600512973181342, 0.7671389889582236, 0.829256542975048, 0.8471274682552217, 0.8898126043169665, 0.7688455229776783, 0.7775112174808656, 0.8498173657819021, 0.840115389801211, 0.7648565657709263, 0.7797926492781206, 0.8532721026074046, 0.827057666804295, 0.8667971123942892, 0.8309885231280625, 0.7689870634905815, 0.7220908746152686, 0.8655854812134591, 0.7314437174613004, 0.7348476706285867, 0.8437625206130726, 0.7512750681394327, 0.8032932617083732, 0.7590379676243508, 0.8595201272819295, 0.838296243098001, 0.8317402394585061, 0.7723557176691114, 0.8482171404616645, 0.8294871706288229, 0.8536893848082574, 0.8740999859437755, 0.6715095641507673, 0.8601316644172858, 0.859726422864922, 0.8128924589433764, 0.8164084138948959, 0.8371335085707998, 0.8511993056879736, 0.77533

In [ ]:
start = time.time()
embed_tsne = TSNE(n_components=2, learning_rate=0.1, n_iter= iterations,verbose=True).fit_transform(X_transformed)
print(f'That took {(time.time()-start):.4f} seconds')
comp, div = LAPS_and_plot(embed_tsne, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], show_fig = True, verbose = False)
print(div)
print(np.mean(np.array(div)))


That took 4.5644 seconds
Getting first time distances for data
Getting first time distances for embedded data
Showing Plot


[0.7865576312899156, 0.8213322868050319, 0.8625498598307595, 0.5842992597840377, 0.7319132772688146, 0.7311600826255609, 0.7335359353650659, 0.8085858811395235, 0.7215424747147412, 0.7842901151235897, 0.7596996780656116, 0.8430830743544435, 0.70607134065542, 0.7463989766168344, 0.761515446421231, 0.7591668648618743, 0.7764695900744765, 0.8515541438890166, 0.758250030308665, 0.6531745568480434, 0.7583755695380114, 0.7540798493951646, 0.7693111569132561, 0.7151248805174455, 0.8538878214910983, 0.7854865484009486, 0.7898475715461628, 0.7704307373384529, 0.7581397416095681, 0.847274180370239, 0.7535120225079284, 0.7855393567366467, 0.8213852719680528, 0.6401198921193016, 0.795800324176835, 0.8230800379007468, 0.6856159720638908, 0.8390249996928019, 0.6621343592429094, 0.8614537048029516, 0.7517712389515876, 0.7646321395961113, 0.6405558713385803, 0.7726623407798832, 0.7479659041033049, 0.6345822650523161, 0.7960391374113835, 0.8171354297009001, 0.6610900926291245, 0.7715554789147558, 0.685

## fSNE (python)

###BREAST CANCER

In [ ]:
fSNE_fast_obj = fSNE_fast(X_transformed, max_iter = iterations, POI=POI, lambdas = 2)
start = time.time()
embed_fsne_fast = fSNE_fast_obj.fit_transform()
print()
print(f'That took {(time.time()-start):.4f} seconds')
comp, div = LAPS_and_plot(embed_fsne_fast, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], show_fig = True, verbose = False)
print(div)
print(f'Average LAPS divergence over all POI : {np.mean(np.array(div)):.5f}')

using cuda
Cost: 2987.502: 100%|██████████| 1/1 [00:00<00:00,  7.85it/s]



That took 1.8812 seconds


 70%|██████▉   | 139/200 [02:38<01:09,  1.14s/it]


KeyboardInterrupt: ignored

In [ ]:
fSNE_fast_obj = fSNE_fast(X_transformed, max_iter = 300, POI=POI, lambdas = 1)
start = time.time()
embed_fsne_fast = fSNE_fast_obj.fit_transform()
print()
print(f'That took {(time.time()-start):.4f} seconds')
comp, div = LAPS_and_plot(embed_fsne_fast, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], show_fig = True, verbose = False)
print(div)
print(f'Average LAPS divergence over all POI : {np.mean(np.array(div)):.5f}')

using cuda
Cost: 679.448: 100%|██████████| 300/300 [00:33<00:00,  9.05it/s]



That took 34.4368 seconds
Getting first time distances for data
Getting first time distances for embedded data
Showing Plot


[0.7869320103033564, 0.7249839285126405, 0.7980048112997709, 0.6091376769934466, 0.6949072786293684, 0.7615269623418952, 0.6655994093749937, 0.776376370411344, 0.7801287899241683, 0.807683108941627, 0.6938391754971969, 0.7152176507374932, 0.7613957523741481, 0.802495894404891, 0.7640989022361877, 0.8235273519734154, 0.7712419453583017, 0.8200251714532598, 0.7967905397710409, 0.6867797249538414, 0.7557354501920441, 0.7181340213216179, 0.8270471812738625, 0.7579605500765232, 0.822704329155858, 0.7548583355609491, 0.761971996038338, 0.7360162165568385, 0.693292075494655, 0.7881938184713562, 0.7514721176864034, 0.8125911275400457, 0.7931315569805972, 0.6847894753007719, 0.733468359277551, 0.7885537921646253, 0.6244003823262313, 0.784466501960494, 0.7590368670973711, 0.8614728175987139, 0.7870921382165688, 0.6673761446014776, 0.7275362842868507, 0.773816652939791, 0.7822545802025698, 0.7305696333581269, 0.7331615920627845, 0.7853235943062249, 0.6293359818310262, 0.7717353134353477, 0.822776

###WINE QUALITY

In [ ]:
fSNE_fast_obj = fSNE_fast(X_transformed, max_iter = iterations, POI=POI, lambdas = 2)
start = time.time()
embed_fsne_fast = fSNE_fast_obj.fit_transform()
print()
print(f'That took {(time.time()-start):.4f} seconds')
comp, div = LAPS_and_plot(embed_fsne_fast, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], show_fig = True, verbose = False)
print(div)
print(f'Average LAPS divergence over all POI : {np.mean(np.array(div)):.5f}')

using cuda
Cost: 9822.324: 100%|██████████| 1000/1000 [03:51<00:00,  4.32it/s]



That took 243.6039 seconds
Getting first time distances for data
Getting first time distances for embedded data
Showing Plot


[0.854007255368685, 0.825036378496999, 0.8642527296298632, 0.8490474257130363, 0.8302382170135427, 0.8573416040496409, 0.781710391064723, 0.8286905614688493, 0.8346797178559953, 0.7373832336234318, 0.6683448070471144, 0.8606860225046542, 0.680964267842116, 0.8118365676318191, 0.8391782476727383, 0.8576060728654393, 0.8100661904756588, 0.7315261713720839, 0.8544571734675372, 0.8370491938714555, 0.7656961089861527, 0.7025627294117893, 0.8779562643429677, 0.7930794510819887, 0.8735584437241108, 0.7772509892902961, 0.7952903645314124, 0.8294484306250822, 0.8775808036677302, 0.6005928965302987, 0.8191899656307793, 0.8533681334712144, 0.8153538570724861, 0.7678900555344148, 0.6703717865361805, 0.8386282831717327, 0.7759326571510046, 0.8653755666061997, 0.7804638843646252, 0.8616140668450558, 0.851385449708697, 0.8838881194501704, 0.8735071706758499, 0.8027084527629005, 0.8623973430676999, 0.8097428009225807, 0.8398658989281238, 0.7880997314488938, 0.8350995081082688, 0.791990314925803, 0.823

In [ ]:
fSNE_fast_obj = fSNE_fast(X_transformed, max_iter = 300, POI=POI, lambdas = 2)
start = time.time()
embed_fsne_fast = fSNE_fast_obj.fit_transform()
print()
print(f'That took {(time.time()-start):.4f} seconds')
comp, div = LAPS_and_plot(embed_fsne_fast, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], show_fig = True, verbose = False)
print(div)
print(f'Average LAPS divergence over all POI : {np.mean(np.array(div)):.5f}')

using cuda
Cost: 9833.912: 100%|██████████| 300/300 [01:12<00:00,  4.12it/s]



That took 85.3460 seconds
Getting first time distances for data
Getting first time distances for embedded data
Showing Plot


[0.856088886788295, 0.8062984148869474, 0.7984182603890908, 0.8510677752130373, 0.8657537276496496, 0.8903069579894645, 0.7491510772468262, 0.8363999734810483, 0.7780900259632699, 0.7373832336234318, 0.7037277633685566, 0.8598830410845872, 0.7142976011754492, 0.8114333396964131, 0.8701834706886162, 0.8577830151205497, 0.8077850030371072, 0.7965357139572753, 0.8617021340884603, 0.8623245526885222, 0.8268706666964885, 0.6629311423645105, 0.8762401747330908, 0.7891627798943877, 0.8743731773145127, 0.7452505152142734, 0.7871990683236103, 0.798018603288124, 0.8790560148076874, 0.6005928965302987, 0.8149646427144208, 0.7824250219238837, 0.81701058907123, 0.7635265699709495, 0.7070935412029229, 0.8063297169350188, 0.8063190121592478, 0.8619679634650537, 0.7763962503042008, 0.8592294884503842, 0.8835539016983884, 0.8902622847733839, 0.8453414876458178, 0.7984149183287661, 0.8572901929808614, 0.8436118721573642, 0.7856808121985335, 0.7866221833461742, 0.8358673107959571, 0.8252780857399025, 0.8

###CREDIT CARD (5000 samples)

In [ ]:
fSNE_fast_obj = fSNE_fast(X_transformed, max_iter = iterations, POI=POI, lambdas = 2)
start = time.time()
embed_fsne_fast = fSNE_fast_obj.fit_transform()
print()
print(f'That took {(time.time()-start):.4f} seconds')
comp, div = LAPS_and_plot(embed_fsne_fast, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], show_fig = True, verbose = False)
print(div)
print(f'Average LAPS divergence over all POI : {np.mean(np.array(div)):.5f}')

using cuda
Cost: 10349.329: 100%|██████████| 1000/1000 [04:42<00:00,  3.54it/s]



That took 300.6485 seconds
Getting first time distances for data
Getting first time distances for embedded data
Showing Plot


[0.8434700730852185, 0.7296260553496703, 0.8513421318079266, 0.8378793303467222, 0.8311427315278328, 0.8333681342113637, 0.671469404736541, 0.7940609632005626, 0.5198089974996796, 0.8350965190751269, 0.7866748755147068, 0.8322025908265676, 0.8176054045111296, 0.7087848001461887, 0.7490001866245133, 0.8013193700287933, 0.8442851015943291, 0.8112185740560676, 0.7661454010090052, 0.8187527979649498, 0.7364678664680782, 0.7765836236777679, 0.6777148916256899, 0.8484021108224897, 0.8294428185827929, 0.7777203435024409, 0.8529357713605503, 0.7961927650083145, 0.848438946719247, 0.8173836142388589, 0.8426200757993367, 0.8054338777543835, 0.8032708775384538, 0.7893339785911258, 0.8470006936233458, 0.8147722327364892, 0.8471898287246189, 0.8632384980928143, 0.8671498995481954, 0.8224080508510032, 0.7161689971640612, 0.6792925873018061, 0.782114643923104, 0.857009221879204, 0.8510350350333737, 0.795321516771641, 0.6876129387635457, 0.6965562754367627, 0.8421644541033484, 0.7772832445935625, 0.78

###MAGIC

In [ ]:
fSNE_fast_obj = fSNE_fast(X_transformed, max_iter = iterations, POI=POI, lambdas = 2)
start = time.time()
embed_fsne_fast = fSNE_fast_obj.fit_transform()
print()
print(f'That took {(time.time()-start):.4f} seconds')
comp, div = LAPS_and_plot(embed_fsne_fast, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], show_fig = True, verbose = False)
print(div)
print(f'Average LAPS divergence over all POI : {np.mean(np.array(div)):.5f}')

using cuda
Cost: 11028.457: 100%|██████████| 1000/1000 [04:45<00:00,  3.50it/s]



That took 303.3714 seconds
Getting first time distances for data
Getting first time distances for embedded data
Showing Plot


[0.8563940514074537, 0.8692249321739158, 0.8722199055412876, 0.8341783818692976, 0.8365685037967219, 0.8416273116717918, 0.8572915151918614, 0.8719732355025962, 0.8833868264774347, 0.8375771688872158, 0.9016773720013833, 0.8759916362613287, 0.8332207209628524, 0.8488709147669682, 0.8510143380759849, 0.6286077361968156, 0.8872727587371947, 0.8237776013104927, 0.8429919500298892, 0.8151503175472556, 0.8521084847381561, 0.774738772154649, 0.8559842812615344, 0.8863995574235253, 0.6973988659985828, 0.6981698123863572, 0.8529718071865937, 0.6792253691935655, 0.7665858709193325, 0.7998927489270893, 0.8403537760052722, 0.7866999978506117, 0.8804654130345586, 0.7659699116017618, 0.7956586252838833, 0.8072215253348078, 0.8711030074150863, 0.8926472524684401, 0.8949976134306477, 0.8018756390450126, 0.8584614193491207, 0.8430630784055626, 0.8053594563058282, 0.8254748489349495, 0.782137224333838, 0.7451062917796449, 0.8391416918420807, 0.8665939008943391, 0.8417345268219469, 0.8903791599211772, 0

In [ ]:
!nvidia-smi

Sat Jul 16 22:16:57 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.32.03    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla P100-PCIE...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   38C    P0    33W / 250W |    791MiB / 16280MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [ ]:
fSNE_para_obj = fSNE_parallel(X_transformed, max_iter = 100, POI=POI, lambdas = 2, cpus = 10)
start = time.time()
embed_fsne_para = fSNE_para_obj.fit_transform()
print(f'That took {(time.time()-start):.4f} seconds')
comp, div = LAPS_and_plot(embed_fsne_para, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], show_fig = True, verbose = False)
print(div)
print(f'Average LAPS divergence over all POI : {np.mean(np.array(div)):.5f}')

#Experiments

In [ ]:
#perplexity = 200
#neighbors = 200
iterations = 1000
perplexities = [10,20,30,40,50]

####Breast Cancer

In [ ]:
percPOI = 0.10

k=50
df = pd.read_csv(Data_path+'breast_cancer.csv')
# df= pd.read_csv(Data_path+'Wine_Quality.csv')
#df = pd.read_csv(Data_path+'Credit_card.csv')
#df = pd.read_csv(Data_path+'Magic.csv')
df = df.fillna(0)
#df = df.sample(5000)
df.reset_index(inplace= True, drop= True)
df.head()
print(df.shape)

model_features, target = Preprocessing.set_features_and_target(df)

y = (df[target].values.reshape(-1, ))
X_df = pd.DataFrame(df, columns=model_features)

np.random.seed(2022)
amountOfPOI = 200
POI = np.random.randint(0, X_df.shape[0], amountOfPOI)

X_transformed, categorical_features, numeric_features, categorical_names = Preprocessing.identify_and_transform_features(df, model_features)

params = [X_df, y, model_features, target, categorical_features, categorical_names, numeric_features, POI]

(569, 31)
Features:  ['radius_mean', 'texture_mean', 'perimeter_mean', 'area_mean', 'smoothness_mean', 'compactness_mean', 'concavity_mean', 'concave points_mean', 'symmetry_mean', 'fractal_dimension_mean', 'radius_se', 'texture_se', 'perimeter_se', 'area_se', 'smoothness_se', 'compactness_se', 'concavity_se', 'concave points_se', 'symmetry_se', 'fractal_dimension_se', 'radius_worst', 'texture_worst', 'perimeter_worst', 'area_worst', 'smoothness_worst', 'compactness_worst', 'concavity_worst', 'concave points_worst', 'symmetry_worst', 'fractal_dimension_worst']
Target:  ['diagnosis']


In [ ]:
# start = time.time()
# embed_tsne = TSNE(n_components=2, learning_rate=0.1, perplexity = 30.0, n_iter= iterations, verbose=True).fit_transform(X_transformed)
# print(f'That took {(time.time()-start):.4f} seconds')
# print(categorical_features)
# comp, div = LAPS_and_plot(embed_tsne, X_transformed,
#               params[0], params[1],
#               params[2], params[3],
#               params[4], params[5],
#               params[6], params[7], show_fig = True, verbose = False)

# print(div)
# print(np.mean(np.array(div)))


In [ ]:
start = time.time()
embed_tsne = sklearnTSNE(n_components=2, n_iter = iterations, perplexity=perplexity).fit_transform(X_transformed)
print(f'That took {(time.time()-start):.4f} seconds')
print(categorical_features)
comp, div = LAPS_and_plot(embed_tsne, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], neighbors=neighbors, show_fig = True, verbose = False)

print(div)
print(np.mean(np.array(div)))

That took 5.8442 seconds
[]


100%|██████████| 200/200 [06:35<00:00,  1.98s/it]

Showing Plot


[0.6580088348921864, 0.6428569776552826, 0.671858999076426, 0.6225722939045936, 0.6258450908479334, 0.6427922847139923, 0.6508362818329714, 0.597059737270213, 0.6217589075580403, 0.6064499617313188, 0.6491198448151164, 0.6611280043177348, 0.6150475597596503, 0.6364933820648837, 0.6308251857818519, 0.6646129724735192, 0.6505674709543133, 0.6555511938124018, 0.6498518526588116, 0.6181065750562353, 0.6517767645379484, 0.658275536481777, 0.6208242690099749, 0.6384791675500756, 0.6433651797988891, 0.6542215388610871, 0.6673706237256372, 0.6584721149570247, 0.6306728838952095, 0.652703082458475, 0.6490082033774893, 0.6703020577079409, 0.6688980701752698, 0.6218016372354043, 0.6183176104810626, 0.6239105403420546, 0.658585088982194, 0.6439988957790386, 0.6260827715502888, 0.6379072744787952, 0.6478324326435174, 0.64285088934143, 0.6473379196336733, 0.6414236154267271, 0.6183184155436051, 0.6374493724349146, 0.6294881200247326, 0.6305202959325314, 0.6248168833789927, 0.6416748348232812, 0.6504

In [ ]:
fSNE_fast_obj = fSNE_fast(X_transformed, max_iter = iterations, POI=POI, perp = perplexity, lambdas = 2)
start = time.time()
embed_fsne_fast = fSNE_fast_obj.fit_transform()
print()
print(f'That took {(time.time()-start):.4f} seconds')
comp, div = LAPS_and_plot(embed_fsne_fast, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], neighbors = neighbors, show_fig = True, verbose = False)
print(div)
print(f'Average LAPS divergence over all POI : {np.mean(np.array(div)):.5f}')

using cuda
Cost: 254.18228:  34%|███▍      | 340/1000 [00:38<01:15,  8.73it/s]



No progress in the last 300 iterations

That took 40.8056 seconds


100%|██████████| 200/200 [06:33<00:00,  1.97s/it]

Showing Plot


[0.6667122589109746, 0.6430226455877517, 0.6714932912773244, 0.6287161737458056, 0.6261048298983979, 0.6383601256054168, 0.6376077738366648, 0.6299175159818677, 0.6808013180501211, 0.6501604748769374, 0.6538167096859092, 0.6812046317411842, 0.683626987070937, 0.6471088467846423, 0.6283998562715167, 0.6787490821531807, 0.6822144366840464, 0.6667342846432828, 0.6412203144625331, 0.6458657653759383, 0.6665924952032924, 0.6322595250095211, 0.6538376126689894, 0.6462618622476362, 0.633386128322673, 0.6596651066692089, 0.6688774691334023, 0.6576253576138515, 0.6264348419148043, 0.6849380576713254, 0.6892477106118438, 0.6551724590030592, 0.6918899574068619, 0.655570781366851, 0.6256244647826468, 0.6377000592904828, 0.6551242577174614, 0.6778431243247627, 0.6258605993487478, 0.6263781059098827, 0.6541793192597596, 0.6379665234819242, 0.6603287033006646, 0.6357798083154899, 0.6402954517431563, 0.6282330097760768, 0.6672657924901266, 0.6457076325867058, 0.6496619763742221, 0.6376299987657201, 0.

#### Credit Card

In [ ]:
percPOI = 0.10

k=50
#df = pd.read_csv(Data_path+'breast_cancer.csv')
df = pd.read_csv(Data_path+'Credit_card.csv')
#df= pd.read_csv(Data_path+'Wine_Quality.csv')
#df = pd.read_csv(Data_path+'Magic.csv')
df = df.fillna(0)
df = df.sample(10000)
df.reset_index(inplace= True, drop= True)
df.head()
print(df.shape)

model_features, target = Preprocessing.set_features_and_target(df)

y = (df[target].values.reshape(-1, ))
X_df = pd.DataFrame(df, columns=model_features)

np.random.seed(2022)
amountOfPOI = 200
POI = np.random.randint(0, X_df.shape[0], amountOfPOI)

X_transformed, categorical_features, numeric_features, categorical_names = Preprocessing.identify_and_transform_features(df, model_features)

params = [X_df, y, model_features, target, categorical_features, categorical_names, numeric_features, POI]

(10000, 24)
Features:  ['LIMIT_BAL', 'SEX', 'EDUCATION', 'MARRIAGE', 'AGE', 'PAY_0', 'PAY_2', 'PAY_3', 'PAY_4', 'PAY_5', 'PAY_6', 'BILL_AMT1', 'BILL_AMT2', 'BILL_AMT3', 'BILL_AMT4', 'BILL_AMT5', 'BILL_AMT6', 'PAY_AMT1', 'PAY_AMT2', 'PAY_AMT3', 'PAY_AMT4', 'PAY_AMT5', 'PAY_AMT6']
Target:  ['default_payment_next_month']


In [ ]:
# start = time.time()
# embed_tsne = TSNE(n_components=2, learning_rate=0.1, perplexity = 30.0, n_iter= iterations,verbose=True).fit_transform(X_transformed)
# print(f'That took {(time.time()-start):.4f} seconds')
# print(categorical_features)
# comp, div = LAPS_and_plot(embed_tsne, X_transformed,
#               params[0], params[1],
#               params[2], params[3],
#               params[4], params[5],
#               params[6], params[7], show_fig = True, verbose = False)

# print(div)
# print(np.mean(np.array(div)))


In [ ]:
start = time.time()
embed_tsne = sklearnTSNE(n_components=2, n_iter = iterations, perplexity=10).fit_transform(X_transformed)
print(f'That took {(time.time()-start):.4f} seconds')
#print(categorical_features)
# comp, div = LAPS_and_plot(embed_tsne, X_transformed,
#               params[0], params[1],
#               params[2], params[3],
#               params[4], params[5],
#               params[6], params[7], neighbors=10, show_fig = True, verbose = False)

# print(div)
# print(np.mean(np.array(div)))
#def LAPS_and_plot(embedding, data_transformed, data_df, y_res, model_feats, targ, cat_feats, cat_names, num_feats, points, neighbors = 20, show_fig = False, verbose = False):
#params = [X_df, y, model_features, target, categorical_features, categorical_names, numeric_features, POI]
#def GAPS_score(embedding, data_df, data_transformed, model_feats, target, cat_feats, cat_names, num_feats, POI = None, show_fig = False, verbose = False):
comp, div, POI = GAPS_score(embed_tsne, params[0], X_transformed, params[2], params[3], params[4], params[5], params[6], params[7])

That took 42.2893 seconds


IndexError: ignored

In [ ]:
fSNE_fast_obj = fSNE_fast(X_transformed, max_iter = iterations, POI=POI, perp = perplexity, lambdas = 2)
start = time.time()
embed_fsne_fast = fSNE_fast_obj.fit_transform()
print()
print(f'That took {(time.time()-start):.4f} seconds')
comp, div = LAPS_and_plot(embed_fsne_fast, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], neighbors = neighbors, show_fig = True, verbose = False)
print(div)
print(f'Average LAPS divergence over all POI : {np.mean(np.array(div)):.5f}')

NameError: ignored

####Wine Quality

In [ ]:
percPOI = 0.10

k=50
#df = pd.read_csv(Data_path+'breast_cancer.csv')
#df = pd.read_csv(Data_path+'Credit_card.csv')
df= pd.read_csv(Data_path+'Wine_Quality.csv')
#df = pd.read_csv(Data_path+'Magic.csv')
df = df.fillna(0)
#df = df.sample(10000)
df.reset_index(inplace= True, drop= True)
df.head()
print(df.shape)

model_features, target = Preprocessing.set_features_and_target(df)

y = (df[target].values.reshape(-1, ))
X_df = pd.DataFrame(df, columns=model_features)

np.random.seed(2022)
amountOfPOI = 200
POI = np.random.randint(0, X_df.shape[0], amountOfPOI)

X_transformed, categorical_features, numeric_features, categorical_names = Preprocessing.identify_and_transform_features(df, model_features)

params = [X_df, y, model_features, target, categorical_features, categorical_names, numeric_features, POI]

(3918, 12)
Features:  ['fixed.acidity', 'volatile.acidity', 'citric.acid', 'residual.sugar', 'chlorides', 'free.sulfur.dioxide', 'total.sulfur.dioxide', 'density', 'pH', 'sulphates', 'alcohol']
Target:  ['quality']


In [ ]:
# start = time.time()
# embed_tsne = TSNE(n_components=2, perplexity = 30.0, n_iter= iterations,verbose=True).fit_transform(X_transformed)
# print(f'That took {(time.time()-start):.4f} seconds')
# print(categorical_features)
# comp, div = LAPS_and_plot(embed_tsne, X_transformed,
#               params[0], params[1],
#               params[2], params[3],
#               params[4], params[5],
#               params[6], params[7], show_fig = True, verbose = False)

# print(div)
# print(np.mean(np.array(div)))


In [ ]:
start = time.time()
embed_tsne = sklearnTSNE(n_components=2, n_iter = iterations, perplexity=perplexity).fit_transform(X_transformed)
print(f'That took {(time.time()-start):.4f} seconds')
print(categorical_features)
comp, div = LAPS_and_plot(embed_tsne, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], neighbors=neighbors, show_fig = True, verbose = False)

print(div)
print(np.mean(np.array(div)))

That took 40.4233 seconds
[]


100%|██████████| 200/200 [02:25<00:00,  1.38it/s]

Showing Plot


[0.7406014427119493, 0.6945282526990864, 0.7972266378463431, 0.7442207882933745, 0.7169845616259146, 0.8490112037238952, 0.7678645470696146, 0.7963221944907557, 0.8054072240366592, 0.7766320065123384, 0.6665092912387185, 0.7691672588227667, 0.7754374525297718, 0.7803657545060877, 0.7315950896521497, 0.7919257600236166, 0.7638494745662948, 0.7905532639100323, 0.7063394952867578, 0.7207819034237517, 0.7507398402591853, 0.6909098004114536, 0.7674945969433473, 0.7770014198692278, 0.8180875701652852, 0.7499034452673592, 0.7513729871576145, 0.739147773654031, 0.8411208446322621, 0.7253675430441837, 0.7862420327543986, 0.7485611054958363, 0.8048153051462744, 0.7366224548892185, 0.6995507291650535, 0.7409125514793626, 0.7704886127374329, 0.7962800771223159, 0.7703919725856476, 0.773681441588687, 0.7298891575891372, 0.7471164087246479, 0.7268303132142924, 0.7694940934200805, 0.817460406614861, 0.7607256503377888, 0.7343086014874283, 0.7400430057387868, 0.7092392767041977, 0.6738974263714974, 0.

In [ ]:
fSNE_fast_obj = fSNE_fast(X_transformed, max_iter = iterations, POI=POI, perp = perplexity, lambdas = 2)
start = time.time()
embed_fsne_fast = fSNE_fast_obj.fit_transform()
print()
print(f'That took {(time.time()-start):.4f} seconds')
comp, div = LAPS_and_plot(embed_fsne_fast, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], neighbors = neighbors, show_fig = True, verbose = False)
print(div)
print(f'Average LAPS divergence over all POI : {np.mean(np.array(div)):.5f}')

using cuda
Cost: 6976.83036: 100%|██████████| 1000/1000 [03:27<00:00,  4.81it/s]



That took 226.9448 seconds


100%|██████████| 200/200 [02:25<00:00,  1.37it/s]

Showing Plot


[0.7543672444774191, 0.7408747998578229, 0.8521037777312778, 0.8050623012691382, 0.7704215688818159, 0.8068110984532966, 0.7850641502199377, 0.7977203738593738, 0.8349065318569528, 0.7603461751973581, 0.6872651837246717, 0.8078686448671051, 0.7737012954397444, 0.8099993130525511, 0.8035733514677118, 0.8846479082221204, 0.7908530936891459, 0.7659578317121559, 0.7620124488067214, 0.7179876159319643, 0.7589422595472397, 0.7432686059817687, 0.783566873297893, 0.8221823029124106, 0.8253028830926812, 0.7622597836587693, 0.7504365269755497, 0.7833875134720023, 0.822673076723399, 0.7392367758840945, 0.8008861806131184, 0.7797778424515868, 0.8032889229385073, 0.8120297326577639, 0.735156805173901, 0.7542139329160484, 0.8194511990134241, 0.8583083123249524, 0.8124419867481333, 0.7780603693457231, 0.7717870209384957, 0.8072774195193473, 0.7693242570441038, 0.8501485004858335, 0.7793454300098633, 0.7852474511358625, 0.8586761401189423, 0.7362031219454039, 0.7726623997392563, 0.7360481114302639, 0.

#### Magic

In [ ]:
percPOI = 0.10

k=50
#df = pd.read_csv(Data_path+'breast_cancer.csv')
#df = pd.read_csv(Data_path+'Credit_card.csv')
#df= pd.read_csv(Data_path+'Wine_Quality.csv')
df = pd.read_csv(Data_path+'Magic.csv')
df = df.fillna(0)
df = df.sample(10000)
df.reset_index(inplace= True, drop= True)
df.head()
print(df.shape)

model_features, target = Preprocessing.set_features_and_target(df)

y = (df[target].values.reshape(-1, ))
X_df = pd.DataFrame(df, columns=model_features)

np.random.seed(2022)
amountOfPOI = 200
POI = np.random.randint(0, X_df.shape[0], amountOfPOI)

X_transformed, categorical_features, numeric_features, categorical_names = Preprocessing.identify_and_transform_features(df, model_features)

params = [X_df, y, model_features, target, categorical_features, categorical_names, numeric_features, POI]

(10000, 11)
Features:  ['fLength', 'fWidth', 'fSize', 'fConc', 'fConc1', 'fAsym', 'fM3Long', 'fM3Trans', 'fAlpha', 'fDist']
Target:  ['class']


In [ ]:
# start = time.time()
# embed_tsne = TSNE(n_components=2, perplexity = 30.0, n_iter= iterations,verbose=True).fit_transform(X_transformed)
# print(f'That took {(time.time()-start):.4f} seconds')
# print(categorical_features)
# comp, div = LAPS_and_plot(embed_tsne, X_transformed,
#               params[0], params[1],
#               params[2], params[3],
#               params[4], params[5],
#               params[6], params[7], show_fig = True, verbose = False)

# print(div)
# print(np.mean(np.array(div)))


In [ ]:
start = time.time()
embed_tsne = sklearnTSNE(n_components=2, n_iter = iterations, perplexity=perplexity).fit_transform(X_transformed)
print(f'That took {(time.time()-start):.4f} seconds')
print(categorical_features)
comp, div = LAPS_and_plot(embed_tsne, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], neighbors=neighbors, show_fig = True, verbose = False)

print(div)
print(np.mean(np.array(div)))

That took 119.0560 seconds
[]


100%|██████████| 200/200 [02:14<00:00,  1.49it/s]

Showing Plot


[0.6988128365000965, 0.6552949654653915, 0.6971025397949875, 0.7408110688652582, 0.6956980051171561, 0.8453940897705234, 0.8653464142677989, 0.8077646637880443, 0.7949552760026812, 0.6963754197214173, 0.8423707964961544, 0.8499903885571761, 0.7618722353656393, 0.8335778839652281, 0.7657551018335287, 0.7744085914193957, 0.6799434197548186, 0.8320919375406294, 0.7554946153155252, 0.7254197163721281, 0.8710866394324112, 0.8265032212398884, 0.7255066311908598, 0.7584386166289201, 0.6940827594258441, 0.8389169114043596, 0.7701516262991599, 0.8060179819431157, 0.6605183480015827, 0.6641392848205009, 0.8888068317583842, 0.7254156555514658, 0.7768643983193697, 0.6579827986872977, 0.7453744960296755, 0.8173405949000184, 0.7175184556260615, 0.8343805215710879, 0.8508464372972138, 0.8457558147121353, 0.8730007798225622, 0.8444053999346622, 0.7835620612296044, 0.7645727899291967, 0.8346163949863094, 0.854393109239769, 0.8049014680889786, 0.7780317193507348, 0.805821687542162, 0.724693249229238, 0.

In [ ]:
fSNE_fast_obj = fSNE_fast(X_transformed, max_iter = iterations, POI=POI, perp = perplexity, lambdas = 2)
start = time.time()
embed_fsne_fast = fSNE_fast_obj.fit_transform()
print()
print(f'That took {(time.time()-start):.4f} seconds')
comp, div = LAPS_and_plot(embed_fsne_fast, X_transformed,
              params[0], params[1],
              params[2], params[3],
              params[4], params[5],
              params[6], params[7], neighbors = neighbors, show_fig = True, verbose = False)
print(div)
print(f'Average LAPS divergence over all POI : {np.mean(np.array(div)):.5f}')

using cuda
Cost: 18322.81900: 100%|██████████| 1000/1000 [11:21<00:00,  1.47it/s]



That took 761.7559 seconds


100%|██████████| 200/200 [02:13<00:00,  1.49it/s]

Showing Plot


[0.7097092703202412, 0.6568902424381005, 0.7178952696114411, 0.7865395109470061, 0.7238220943083892, 0.7739634346000845, 0.8555106680526338, 0.8497341495610027, 0.8032637352307014, 0.7527049796498215, 0.8658041017260564, 0.8523549006280328, 0.8551766578604165, 0.8154437808780778, 0.8385759092432895, 0.8320401142747961, 0.6768932388958648, 0.8617905524957156, 0.8395356040645076, 0.6960208763560847, 0.8690278720786094, 0.835149035541578, 0.7892699840421297, 0.7833967145560139, 0.6973111278349591, 0.8600848427565383, 0.8215024847600534, 0.7989256086471285, 0.7112475945073139, 0.7131595485930688, 0.879753953654545, 0.7545468055800805, 0.8212195669686335, 0.6633090768746635, 0.8320187944847389, 0.8216599177606292, 0.7104651049152378, 0.8403420925669998, 0.8556159920032884, 0.8342781038924746, 0.8801838026138719, 0.8254855679051286, 0.8252288604395359, 0.8493747141392105, 0.8451118240919354, 0.8458307319554931, 0.8145711557222339, 0.8623012464295473, 0.8611074693926205, 0.8692598248838257, 0

####Spam Data

In [ ]:
percPOI = 0.10

k=50
df = pd.DataFrame(spam_data)
df = df.fillna(0)
df.reset_index(inplace= True, drop= True)
df.head()
print(df.shape)

model_features, target = Preprocessing.set_features_and_target(df)

y = (df[target].values.reshape(-1, ))
X_df = pd.DataFrame(df, columns=model_features)

np.random.seed(2022)
amountOfPOI = 100
POI = np.random.randint(0, X_df.shape[0], amountOfPOI)

X_transformed, categorical_features, numeric_features, categorical_names = Preprocessing.identify_and_transform_features(df, model_features)

params = [X_df, y, model_features, target, categorical_features, categorical_names, numeric_features, POI]

(5572, 101)
Features:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99]
Target:  [100]


In [ ]:
perplexities = [5, 10, 20]
for p in perplexities:
  start = time.time()
  embed_tsne = sklearnTSNE(n_components=2, n_iter = iterations, perplexity=perplexity).fit_transform(X_transformed)
  print(f'That took {(time.time()-start):.4f} seconds')
  print(categorical_features)
  comp, div = LAPS_and_plot(embed_tsne, X_transformed,
                params[0], params[1],
                params[2], params[3],
                params[4], params[5],
                params[6], params[7], neighbors=neighbors, show_fig = True, verbose = False)

  #print(div)
  print('sklearn TSNE')
  print(f'Average LAPS divergence over all POI : {np.mean(np.array(div)):.5f} with perplexity {p}')

  fSNE_fast_obj = fSNE_fast(X_transformed, max_iter = iterations, POI=POI, perp = p, lambdas = 2)
  start = time.time()
  embed_fsne_fast = fSNE_fast_obj.fit_transform()
  print()
  print(f'That took {(time.time()-start):.4f} seconds')
  comp, div = LAPS_and_plot(embed_fsne_fast, X_transformed,
                params[0], params[1],
                params[2], params[3],
                params[4], params[5],
                params[6], params[7], neighbors = p, show_fig = True, verbose = False)
  #print(div)
  print('fSNE')
  print(f'Average LAPS divergence over all POI : {np.mean(np.array(div)):.5f} with perplexity {p}')

That took 70.1039 seconds
[]


100%|██████████| 100/100 [06:42<00:00,  4.02s/it]

Showing Plot


using cuda


sklearn TSNE
Average LAPS divergence over all POI : 0.66616 with perplexity 5


...

Cost: 50489.21009:  22%|██▏       | 224/1000 [01:21<04:40,  2.76it/s]



An unexpected error occured
C = nan

That took 104.5777 seconds


100%|██████████| 100/100 [05:37<00:00,  3.37s/it]

Showing Plot


fSNE
Average LAPS divergence over all POI : 0.74661 with perplexity 20


####Sentiment Data

In [ ]:
percPOI = 0.10

k=50
df = pd.DataFrame(sentiment_data)
df = df.fillna(0)
df.reset_index(inplace= True, drop= True)
df.head()
print(df.shape)

model_features, target = Preprocessing.set_features_and_target(df)

y = (df[target].values.reshape(-1, ))
X_df = pd.DataFrame(df, columns=model_features)

np.random.seed(2022)
amountOfPOI = 100
POI = np.random.randint(0, X_df.shape[0], amountOfPOI)

X_transformed, categorical_features, numeric_features, categorical_names = Preprocessing.identify_and_transform_features(df, model_features)

params = [X_df, y, model_features, target, categorical_features, categorical_names, numeric_features, POI]

(10000, 101)
Features:  [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99]
Target:  [100]


In [ ]:
perplexities = [5, 10, 20]
for p in perplexities:
  start = time.time()
  embed_tsne = sklearnTSNE(n_components=2, n_iter = iterations, perplexity=perplexity).fit_transform(X_transformed)
  print(f'That took {(time.time()-start):.4f} seconds')
  print(categorical_features)
  comp, div = LAPS_and_plot(embed_tsne, X_transformed,
                params[0], params[1],
                params[2], params[3],
                params[4], params[5],
                params[6], params[7], neighbors=neighbors, show_fig = True, verbose = False)

  #print(div)
  print('sklearn TSNE')
  print(f'Average LAPS divergence over all POI : {np.mean(np.array(div)):.5f} with perplexity {p}')

  fSNE_fast_obj = fSNE_fast(X_transformed, max_iter = iterations, POI=POI, perp = p, lambdas = 2)
  start = time.time()
  embed_fsne_fast = fSNE_fast_obj.fit_transform()
  print()
  print(f'That took {(time.time()-start):.4f} seconds')
  comp, div = LAPS_and_plot(embed_fsne_fast, X_transformed,
                params[0], params[1],
                params[2], params[3],
                params[4], params[5],
                params[6], params[7], neighbors = p, show_fig = True, verbose = False)
  #print(div)
  print('fSNE')
  print(f'Average LAPS divergence over all POI : {np.mean(np.array(div)):.5f} with perplexity {p}')

That took 112.8903 seconds
[]


100%|██████████| 100/100 [06:48<00:00,  4.09s/it]

Showing Plot


using cuda


sklearn TSNE
Average LAPS divergence over all POI : 0.70621 with perplexity 5


...

100%|██████████| 100/100 [05:32<00:00,  3.33s/it]

Showing Plot


fSNE
Average LAPS divergence over all POI : 0.73422 with perplexity 10
That took 114.1873 seconds
[]


 17%|█▋        | 17/100 [01:20<06:31,  4.72s/it]


KeyboardInterrupt: ignored

In [ ]:
perplexities = [5, 10, 20]
for p in perplexities:
  # start = time.time()
  # embed_tsne = sklearnTSNE(n_components=2, n_iter = iterations, perplexity=perplexity).fit_transform(X_transformed)
  # print(f'That took {(time.time()-start):.4f} seconds')
  # print(categorical_features)
  # comp, div = LAPS_and_plot(embed_tsne, X_transformed,
  #               params[0], params[1],
  #               params[2], params[3],
  #               params[4], params[5],
  #               params[6], params[7], neighbors=neighbors, show_fig = True, verbose = False)

  # #print(div)
  # print('sklearn TSNE')
  # print(f'Average LAPS divergence over all POI : {np.mean(np.array(div)):.5f} with perplexity {p}')

  fSNE_fast_obj = fSNE_fast(X_transformed, max_iter = iterations, POI=POI, perp = p, lambdas = 2)
  start = time.time()
  embed_fsne_fast = fSNE_fast_obj.fit_transform()
  print()
  print(f'That took {(time.time()-start):.4f} seconds')
  comp, div = LAPS_and_plot(embed_fsne_fast, X_transformed,
                params[0], params[1],
                params[2], params[3],
                params[4], params[5],
                params[6], params[7], neighbors = p, show_fig = True, verbose = False)
  #print(div)
  print('fSNE')
  print(f'Average LAPS divergence over all POI : {np.mean(np.array(div)):.5f} with perplexity {p}')

#Results:

Spam_Data
Max 10K samples, around 100 POI used in LAPS score.

Dataset       | sklearnTSNE    | fSNE
--------------|----------------|-------------
Perplexity 5  | 0.66616        | 0.60282
Perplexity 10 | 0.66564        | 0.69729
Perplexity 20 | 0.66566        | 0.74661   <- nan error

Sentiment_data
Max 10K samples, around 100 POI used in LAPS score.

Dataset       | sklearnTSNE    | fSNE
--------------|----------------|-------------
Perplexity 5  | 0.70621        |
Perplexity 10 |         |
Perplexity 20 |         |


Max 10K samples, 50 perplexity and 50 neighbors around 200 POI used in LAPS score.

Dataset       | sklearnTSNE    | fSNE
--------------|----------------|-------------
Breast Cancer | 0.71562        | 0.73252
Credit Card   | 0.77077        | 0.80490
Wine Quality  | 0.77986        | 0.83121
Magic         | 0.77766        | 0.84147

Max 10K samples, 100 perplexity and 100 neighbors around 200 POI used in LAPS score.

Dataset       | sklearnTSNE    | fSNE
--------------|----------------|-------------
Breast Cancer | 0.68203        | 0.69498
Credit Card   | 0.76119        | 0.79204
Wine Quality  | 0.78201        | 0.81238
Magic         | 0.79191        | 0.83160

Max 10K samples, 200 perplexity and 200 neighbors around 200 POI used in LAPS score.

Dataset       | sklearnTSNE    | fSNE
--------------|----------------|-------------
Breast Cancer | 0.64308        | 0.65066
Credit Card   | 0.73852        | 0.75978
Wine Quality  | 0.75790        | 0.78074
Magic         | 0.77394        | 0.80533



In [ ]:
DR_algorithms.run_DR_Algorithm('PCA', X_transformed)

array([[ 2.20929547,  0.80846445],
       [-0.40434274,  0.9659229 ],
       [-0.92981753,  1.33006635],
       ...,
       [-3.36984713,  0.3355617 ],
       [-1.62447864, -1.71988687],
       [-3.7140753 ,  0.6996603 ]])

In [ ]:
DR_algorithms.run_DR_Algorithm('Trimap', X_transformed)

array([[ 38.44439   ,   3.1527371 ],
       [ -7.4559183 ,   0.21758048],
       [-21.880959  ,  27.617754  ],
       ...,
       [-42.252453  ,   3.373934  ],
       [-25.70871   , -26.939602  ],
       [-42.631622  ,   3.4451983 ]], dtype=float32)

In [ ]:
DR_algorithms.run_DR_Algorithm('MDS', X_transformed)

array([[-2.17173459,  1.13772291],
       [ 0.4116464 ,  1.46256936],
       [-1.2195012 ,  1.49663721],
       ...,
       [ 0.16590049,  1.4221769 ],
       [-1.92333916,  1.53815513],
       [ 1.39071221, -1.86284022]])

In [ ]:
DR_algorithms.run_DR_Algorithm('Isomap', X_transformed)

array([[ 3.43801286,  0.86974634],
       [ 1.81221716, -1.86129162],
       [ 4.29912079,  0.08960746],
       ...,
       [ 1.20874861, -1.74139967],
       [ 4.71962416, -0.22125747],
       [-3.82383547, -0.62025297]])

In [ ]:
DR_algorithms.run_DR_Algorithm('KernelPCA', X_transformed)

array([[ 1.97743145,  0.49221721],
       [ 0.76041241, -1.04740054],
       [ 1.76466817, -0.08551636],
       ...,
       [ 0.81746334, -0.68971204],
       [ 2.25278088,  0.37472723],
       [-1.78235947,  0.03972097]])

In [ ]:
!pip uninstall umap
!pip install umap-learn

Found existing installation: umap 0.1.1
Uninstalling umap-0.1.1:
  Would remove:
    /usr/local/lib/python3.7/dist-packages/umap-0.1.1.dist-info/*
    /usr/local/lib/python3.7/dist-packages/umap/*
Proceed (y/n)? y
  Successfully uninstalled umap-0.1.1
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 88 kB 3.5 MB/s 
     |████████████████████████████████| 1.1 MB 24.7 MB/s 
  Created wheel for umap-learn: filename=umap_learn-0.5.3-py3-none-any.whl size=82829 sha256=9d75028da90ab2cfe520899ce31367a77c886bb9c5b65e2a8cdbf07a9a8eb09e
  Stored in directory: /root/.cache/pip/wheels/b3/52/a5/1fd9e3e76a7ab34f134c07469cd6f16e27ef3a37aeff1fe821
  Created wheel for pynndescent: filename=pynndescent-0.5.7-py3-none-any.whl size=54286 sha256=099e768f40e1c59f9393dd736bd40dc0e915327efffbaada38e02f0863ee3509
  Stored in directory: /root/.cache/pip/wheels/7f/2a/f8/7bd5dcec71bd5c669f6f574db3113513696b98f3f9b51f496c
Suc

In [ ]:
import umap.umap_ as umap
int_dim = 2
reducer = umap.UMAP(n_neighbors=15, n_components=int_dim)
points = reducer.fit_transform(X_transformed)

In [ ]:
print(points)

[[1.5252904 5.886136 ]
 [3.5980237 7.8248606]
 [1.6340543 6.5273285]
 ...
 [2.9184985 8.405101 ]
 [1.1500268 6.531172 ]
 [9.721827  7.800466 ]]
